# P15.1 - Mapping Accidents - review

Boilerplate imports

In [2]:
# Import the required libraries and open the connection to Mongo
import collections
import datetime
import matplotlib as mpl
mpl.rcParams['figure.figsize'] = (15,15) # reset the base size of figure.

import pandas as pd
import scipy.stats

import folium

import pymongo
from bson.objectid import ObjectId
from bson.son import SON

In [3]:
# Open a connection to the Mongo server, open the accidents database and name the collections of accidents and labels
client = pymongo.MongoClient('mongodb://localhost:27351/')

db = client.accidents
accidents = db.accidents
labels = db.labels
roads = db.roads

In [4]:
# Load the expanded names of keys and human-readable codes into memory
expanded_name = collections.defaultdict(str)
for e in labels.find({'expanded': {"$exists": True}}):
    expanded_name[e['label']] = e['expanded']
    
label_of = collections.defaultdict(str)
for l in labels.find({'codes': {"$exists": True}}):
    for c in l['codes']:
        try:
            label_of[l['label'], int(c)] = l['codes'][c]
        except ValueError: 
            label_of[l['label'], c] = l['codes'][c]

## Plotting some accidents
To start with, let's just plot some accidents on the map to see how it's done.  Depending on which thousand accidents MongoDB picks, you may need to move and zoom the map to see the points.

In [6]:
# initialize a map
m = folium.Map(location=[55, -3], width=500, height=800, zoom_start=6)

# select 1000 accidents and plot 
for a in accidents.find({}, ['loc.coordinates'], limit=1000):
    folium.RegularPolygonMarker(location=[a['loc']['coordinates'][1],
                                          a['loc']['coordinates'][0]],
                                number_of_sides=5,
                                radius=5,
                                rotation=54).add_to(m)
# show the plot
m

Let's see if we can plot the UK motorway network by where the accidents are.  Road_Class tells us the type of road the accident was on

In [7]:
[(c, l, label_of[l, c]) for l, c in label_of if 'Road_Class' in l]

[(5, '2nd_Road_Class', 'C'),
 (2, '1st_Road_Class', 'A(M)'),
 (0, '2nd_Road_Class', 'Not at junction or within 20 metres'),
 (4, '1st_Road_Class', 'B'),
 (2, '2nd_Road_Class', 'A(M)'),
 (1, '1st_Road_Class', 'Motorway'),
 (6, '1st_Road_Class', 'Unclassified'),
 (4, '2nd_Road_Class', 'B'),
 (3, '1st_Road_Class', 'A'),
 (1, '2nd_Road_Class', 'Motorway'),
 (6, '2nd_Road_Class', 'Unclassified'),
 (5, '1st_Road_Class', 'C'),
 (3, '2nd_Road_Class', 'A')]

This presents a problem - do we include A(M) as motorways?  Let's say yes and include them in the query.

But how many accidents were there?

In [8]:
accidents.find({'$or': [{'1st_Road_Class': 1},
                        {'2nd_Road_Class': 1},
                        {'1st_Road_Class': 2},
                        {'2nd_Road_Class': 2}]}).count()

6274

That's quite a lot.  We don't need that many to show the idea.  We can restrict the subset by date, picking just the accidents in January 2012

In [9]:
accidents.find({'$or': [{'1st_Road_Class': 1},
                        {'2nd_Road_Class': 1},
                        {'1st_Road_Class': 2},
                        {'2nd_Road_Class': 2}],
                'Datetime': {'$lte': datetime.datetime(2012, 1, 31)}}).count()

448

That is a better number for plotting

In [10]:
m = folium.Map(location=[55, -3], width=500, height=800, zoom_start=6)

for a in accidents.find({'$or': [{'1st_Road_Class': 1},
                        {'2nd_Road_Class': 1},
                        {'1st_Road_Class': 2},
                        {'2nd_Road_Class': 2}],
                'Datetime': {'$lte': datetime.datetime(2012, 1, 31)}},
                        ['loc.coordinates']):
    
    folium.RegularPolygonMarker(location=[a['loc']['coordinates'][1],
                                          a['loc']['coordinates'][0]],
                                number_of_sides=5,
                                radius=5,
                                rotation=54).add_to(m)

# show map
m

There is a lot of boilerplate code for adding markers.  So it makes sense to wrap them in a function

In [13]:
def add_accident_markers(the_map, query, limit=0,
                    number_of_sides=5, fill_color='#769d96',
                    radius=5, rotation=54):
    for a in accidents.find(query, ['loc.coordinates'], limit):
        folium.RegularPolygonMarker(location=[a['loc']['coordinates'][1],
                                              a['loc']['coordinates'][0]],
                                    number_of_sides=number_of_sides,
                                    radius=radius,
                                    rotation=rotation).add_to(the_map)

In [14]:
def map_centre_from_points(query):
    latlons = list(zip(*[(a['loc']['coordinates'][1],
                          a['loc']['coordinates'][0]) 
                         for a in accidents.find(query, ['loc.coordinates'])]))
    max_lat = max(latlons[0])
    max_lon = max(latlons[1])
    min_lat = min(latlons[0])
    min_lon = min(latlons[1])
    
    return [min_lat + (max_lat - min_lat) / 2,
            min_lon + (max_lon - min_lon) / 2]

We can now use these functions to map the North Wales police force (code 60)

In [16]:
# define the query
query = {'Police_Force': 60}

# get the map centre
map_centre = map_centre_from_points(query)

# initialize the map
m = folium.Map(map_centre, zoom_start=9)

# add accident markers
add_accident_markers(m, query)

# show the map
m

### Activity 1
Plot the locations of all fatal and serious accidents that occured on motorways.

In [20]:
[(c, l, label_of[l, c]) for l, c in label_of if 'Accident_Severity' in l]

[(3, 'Accident_Severity', 'Slight'),
 (1, 'Accident_Severity', 'Fatal'),
 (2, 'Accident_Severity', 'Serious')]

In [34]:
query = {'$and': [{'$or': [{'1st_Road_Class': 1}, {'2nd_Road_Class': 1},
                           {'1st_Road_Class': 2}, {'2nd_Road_Class': 2}]}, 
                  {'$or': [{'Accident_Severity': 1}, {'Accident_Severity': 2}]}]}

map_centre = map_centre_from_points(query)
m = folium.Map(map_centre, zoom_start=5)

add_accident_markers(m, query)
m                  

In [36]:
# more elegant query
query = {'$or': [{'1st_Road_Class': 1}, {'2nd_Road_Class': 1},
                 {'1st_Road_Class': 2}, {'2nd_Road_Class': 2}],
         'Accident_Severity': {'$in': [1, 2]}}

### Activity 2
Plot the accidents covered by the cornwall local authority.  

In [27]:
# find the code for cornwall
[(c, l, label_of[l, c]) for l, c in label_of if ('Cornwall' in l)]

[]

In [29]:
# try again to find the code for cornwall
[(c, l, label_of[l, c]) for l, c in label_of if 'Cornwall' in label_of[l, c]]

[(596, 'Local_Authority_(District)', 'Cornwall'),
 (593, 'Local_Authority_(District)', 'North Cornwall'),
 (50, 'Police_Force', 'Devon and Cornwall'),
 ('E06000052', 'Local_Authority_(Highway)', 'Cornwall')]

In [33]:
# found it we can use E06000052
query = {'Local_Authority_(Highway)': 'E06000052'}

map_centre = map_centre_from_points(query)

m = folium.Map(map_centre, zoom_start=8)
add_accident_markers(m, query)
m

## Milton Keynes
Let's zoom in a bit on MK the home of Open University.  Let's start by just plotting all the accidents that occurred near MK.

In [37]:
region = {'loc': 
          {'$nearSphere': 
           {'$geometry': 
            {'type': 'Point', 
             'coordinates': [-0.7601851, 52.0395099]},
            '$maxDistance': 10000
           }}}

map_centre = map_centre_from_points(region)

m = folium.Map(map_centre, zoom_start=12)
add_accident_markers(m, region)

In [38]:
m

In [39]:
milton_keynes = {'type': 'Polygon',
                 'coordinates': [[[-0.877025, 52.092317],
                                  [-0.651709, 52.092317],
                                  [-0.651709, 51.958628],
                                  [-0.877025, 51.958268],
                                  [-0.877025, 52.092317]
                                 ]]}

min_mk_lat = min(p[1] for p in milton_keynes['coordinates'][0])
max_mk_lat = max(p[1] for p in milton_keynes['coordinates'][0])
min_mk_lon = min(p[0] for p in milton_keynes['coordinates'][0])
max_mk_lon = max(p[0] for p in milton_keynes['coordinates'][0])

mk_centre = [min_mk_lat + (max_mk_lat - min_mk_lat) / 2, min_mk_lon + (max_mk_lon - min_mk_lon) / 2]

mk_region_query = {'loc': {'$geoWithin': {'$geometry': milton_keynes}}}

In [41]:
m = folium.Map(mk_centre, zoom_start=12)    
add_accident_markers(m, mk_region_query)
m

Let's plot the different accident severities in different colours.

First, a function to merge the additional query terms for the different types into the existing location-specifying query.

In [43]:
def merge_dicts(this, other):
    this_copy = this.copy()
    for k in other:
        this_copy[k] = other[k]
    return this_copy

# Use like:
a_dict = {'k1': 1, 'k2': 2}
merge_dicts(a_dict, {'add1': 100})

{'add1': 100, 'k1': 1, 'k2': 2}

In [45]:
m = folium.Map(mk_centre, zoom_start=12) 

add_accident_markers(m, merge_dicts(mk_region_query, {'Accident_Severity': 1}),
    fill_color='#ff0000', number_of_sides=5, radius=10, rotation=54)

add_accident_markers(m, merge_dicts(mk_region_query, {'Accident_Severity': 2}),
    fill_color='#ffff00', number_of_sides=4, radius=7, rotation=0)

add_accident_markers(m, merge_dicts(mk_region_query, {'Accident_Severity': 3}),
    fill_color='#00ff00', number_of_sides=3, radius=5, rotation=30)
m

In [46]:
m.save('data/accident_types_MK.html ')

FileNotFoundError: [Errno 2] No such file or directory: 'data/accident_types_MK.html '